# Exploratory analysis

TODO:
- Understanding the reason for fake profiles can bring insight on how to catch them (could be trivial with prior knowledge, e.g., SEO hacking => URLs)
- Make casistics (e.g. author publishing with empty orcid, author publishing but not on OpenAIRE, etc.)
- Temporal dimension of any use?
- Can we access private info thanks to the OpenAIRE-ORCID agreement?


In [1]:
import glob

import pandas as pd
import ast
import tldextract
import numpy as np

import antispam

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

init_notebook_mode(connected=True)
TOP_N = 0
TOP_RANGE = [0, 0]

def set_top_n(n):
    global TOP_N, TOP_RANGE
    TOP_N = n
    TOP_RANGE = [-.5, n - 1 + .5]
    
pd.set_option('display.max_columns', None)

Notable solid ORCID iDs for explorative purposes:

In [2]:
AM = '0000-0002-5193-7851'
PP = '0000-0002-8588-4196'


Notable anomalies:

In [3]:
JOURNAL = '0000-0003-1815-5732'
NOINFO = '0000-0001-5009-2052'
VALID_NO_OA = '0000-0002-5154-6404' # True profile, but not in OpenAIRE
WORK_MISUSE = '0000-0001-7870-1120'
# todo: find group-shared ORCiD, if possible

Notable fake ORCID iDs:

In [4]:
SCAFFOLD = '0000-0001-5004-7761'
WHATSAPP = '0000-0001-6997-9470'
PENIS = '0000-0002-3399-7287'
BITCOIN = '0000-0002-7518-6845'
FITNESS_CHINA = '0000-0002-1234-835X' # URL record + employment
CANNABIS = '0000-0002-9025-8632'      # URL > 70 + works (REMOVED)
PLUMBER = '0000-0002-1700-8311'       # URL > 10 + works 

Load the dataset

In [5]:
parts = glob.glob('../data/processed/dataset.pkl.*')

df = pd.concat((pd.read_pickle(part) for part in sorted(parts)))
df.head(5)

orcid  verified_email  verified_primary_email given_names  \
0  0000-0001-6097-3953           False                   False        <NA>   
1  0000-0001-6112-5550            True                    True        <NA>   
2  0000-0001-6152-2695            True                    True        <NA>   
3  0000-0001-6220-5683            True                    True        <NA>   
4  0000-0001-7071-8294            True                    True        <NA>   

  family_name biography                 other_names primary_email keywords  \
0        <NA>      <NA>                         NaN          <NA>      NaN   
1        <NA>      <NA>  [v.i. yurtaev; v. yurtaev]          <NA>      NaN   
2        <NA>      <NA>                         NaN          <NA>      NaN   
3        <NA>      <NA>                         NaN          <NA>      NaN   
4        <NA>      <NA>                         NaN          <NA>      NaN   

  external_ids education                                         employment  \
0          NaN       NaN                                                NaN   
1          NaN       NaN  [[professor, peoples friendship university of ...   
2          NaN       NaN                                                NaN   
3          NaN       NaN  [[research scientist, new york university abu ...   
4          NaN       NaN  [[researcher (academic), universidad de zarago...   

   n_works works_source           activation_date          last_update_date  \
0        0          NaN  2018-03-02t09:29:16.528z  2018-03-02t09:43:07.551z   
1        0          NaN  2018-04-03t07:50:23.358z  2020-03-18t09:42:44.753z   
2        0          NaN  2019-12-11t15:31:56.388z  2020-01-28t15:34:17.309z   
3        0          NaN  2015-08-18t12:36:45.307z  2020-09-23t13:37:54.180z   
4        0          NaN  2014-03-10t13:22:01.966z  2016-06-14t22:17:54.470z   

   n_doi  n_arxiv  n_pmc  n_other_pids  label primary_email_domain  \
0      0        0      0             0  False                  NaN   
1      0        0      0             0  False                  NaN   
2      0        0      0             0  False                  NaN   
3      0        0      0             0  False                  NaN   
4      0        0      0             0  False                  NaN   

  other_email_domains url_domains  n_emails  n_urls  n_ids  n_keywords  \
0                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   
1                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   
2                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   
3                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   
4                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   

   n_education  n_employment  
0         <NA>          <NA>  
1         <NA>             1  
2         <NA>          <NA>  
3         <NA>             1  
4         <NA>             2

Notable profiles inspection

In [6]:
df[df['orcid'] == AM]

orcid  verified_email  verified_primary_email  \
3073261  0000-0002-5193-7851            True                    True   

        given_names family_name  \
3073261      andrea    mannocci   

                                                 biography other_names  \
3073261  data scientist & researcher; scholarly knowled...         NaN   

                       primary_email  \
3073261  andrea.mannocci@isti.cnr.it   

                                                  keywords  \
3073261  [open science, data science, science of scienc...   

                              external_ids  \
3073261  [[scopus author id, 55233589900]]   

                                                 education  \
3073261  [[information engineering, ph.d., università d...   

                                                employment  n_works  \
3073261  [[research associate, istituto di scienza e te...       37   

                                              works_source  \
3073261  [scopus - elsevier, crossref metadata search, ...   

                  activation_date          last_update_date  n_doi  n_arxiv  \
3073261  2017-09-12t14:28:33.467z  2021-03-17t15:40:07.776z     34        0   

         n_pmc  n_other_pids  label primary_email_domain other_email_domains  \
3073261      0            60   True          isti.cnr.it                 NaN   

                                    url_domains  n_emails  n_urls  n_ids  \
3073261  [github.io, twitter.com, linkedin.com]      <NA>       3      1   

         n_keywords  n_education  n_employment  
3073261           5            4             5

In [7]:
df[df['orcid'] == WHATSAPP]

orcid  verified_email  verified_primary_email  \
9887272  0000-0001-6997-9470            True                    True   

        given_names family_name biography other_names primary_email  \
9887272       other    whatsapp      <NA>         NaN          <NA>   

                                                  keywords external_ids  \
9887272  [whatsapp gb baixar, whatsapp gb 2020, whatsap...          NaN   

        education employment  n_works works_source           activation_date  \
9887272       NaN        NaN        0          NaN  2020-10-07t10:37:12.237z   

                 last_update_date  n_doi  n_arxiv  n_pmc  n_other_pids  label  \
9887272  2020-10-08t02:32:03.935z      0        0      0             0  False   

        primary_email_domain other_email_domains  \
9887272                  NaN                 NaN   

                                               url_domains  n_emails  n_urls  \
9887272  [otherwhatsapp.com, im-creator.com, facebook.c...      <NA>      27   

         n_ids  n_keywords  n_education  n_employment  
9887272   <NA>           4         <NA>          <NA>

In [8]:
df.count()

orcid                     10989649
verified_email            10989649
verified_primary_email    10989649
given_names               10959039
family_name               10671715
biography                   354015
other_names                 554684
primary_email               124722
keywords                    649637
external_ids               1308598
education                  2441645
employment                 2680488
n_works                   10989649
works_source               2740939
activation_date           10989649
last_update_date          10989649
n_doi                     10989649
n_arxiv                   10989649
n_pmc                     10989649
n_other_pids              10989649
label                     10989649
primary_email_domain        124722
other_email_domains          48615
url_domains                 715067
n_emails                     48615
n_urls                      715067
n_ids                      1308598
n_keywords                  649637
n_education         

In [9]:
df['orcid'].describe()

count                10989649
unique               10989649
top       0000-0001-5242-3687
freq                        1
Name: orcid, dtype: object

## Primary email

In [10]:
df['primary_email'].describe()

count                     124722
unique                    124718
top       opercin@erbakan.edu.tr
freq                           2
Name: primary_email, dtype: object

Dupe emails

In [11]:
df['primary_email'].dropna().loc[df['primary_email'].duplicated()]

1681787       opercin@erbakan.edu.tr
5590332     patrick.davey@monash.edu
9316843             maykin@owasp.org
10375852       andycheng2026@163.com
Name: primary_email, dtype: string

In [12]:
df[df['primary_email'] == 'maykin@owasp.org']

orcid  verified_email  verified_primary_email  \
7543981  0000-0002-0836-2271            True                    True   
9316843  0000-0001-9855-1676            True                    True   

        given_names family_name biography other_names     primary_email  \
7543981      maykin    warasart      <NA>         NaN  maykin@owasp.org   
9316843      maykin    warasart      <NA>         NaN  maykin@owasp.org   

        keywords external_ids education employment  n_works works_source  \
7543981      NaN          NaN       NaN        NaN        0          NaN   
9316843      NaN          NaN       NaN        NaN        0          NaN   

                  activation_date          last_update_date  n_doi  n_arxiv  \
7543981  2020-09-15t04:43:55.709z  2020-09-15t05:17:28.509z      0        0   
9316843  2020-10-23t17:51:51.925z  2021-01-01t15:00:52.053z      0        0   

         n_pmc  n_other_pids  label primary_email_domain  \
7543981      0             0  False            owasp.org   
9316843      0             0  False            owasp.org   

           other_email_domains url_domains  n_emails  n_urls  n_ids  \
7543981            [dga.or.th]         NaN         1    <NA>   <NA>   
9316843  [dga.or.th, ieee.org]         NaN         2    <NA>   <NA>   

         n_keywords  n_education  n_employment  
7543981        <NA>         <NA>          <NA>  
9316843        <NA>         <NA>          <NA>

In [13]:
df[df['primary_email'] == 'opercin@erbakan.edu.tr']

orcid  verified_email  verified_primary_email  \
347852   0000-0002-2232-9638            True                    True   
1681787  0000-0003-0033-0918            True                    True   

        given_names family_name biography other_names           primary_email  \
347852        osman      perçin      <NA>         NaN  opercin@erbakan.edu.tr   
1681787       osman      perçin      <NA>         NaN  opercin@erbakan.edu.tr   

        keywords external_ids education  \
347852       NaN          NaN       NaN   
1681787      NaN          NaN       NaN   

                                                employment  n_works  \
347852                                                 NaN        0   
1681787  [[, necmettin erbakan university, konya, , tr,...        0   

        works_source           activation_date          last_update_date  \
347852           NaN  2015-01-12t13:47:55.549z  2020-01-27t07:38:24.269z   
1681787          NaN  2015-10-13t05:47:12.014z  2020-12-25t13:52:03.976z   

         n_doi  n_arxiv  n_pmc  n_other_pids  label primary_email_domain  \
347852       0        0      0             0  False       erbakan.edu.tr   
1681787      0        0      0             0  False       erbakan.edu.tr   

        other_email_domains url_domains  n_emails  n_urls  n_ids  n_keywords  \
347852                  NaN         NaN      <NA>    <NA>   <NA>        <NA>   
1681787                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   

         n_education  n_employment  
347852          <NA>          <NA>  
1681787         <NA>             1

In [14]:
df[df['primary_email'] == 'patrick.davey@monash.edu']

orcid  verified_email  verified_primary_email  \
954085   0000-0002-9158-1757            True                    True   
5590332  0000-0002-8774-0030            True                    True   

        given_names family_name biography other_names  \
954085      patrick       davey      <NA>         NaN   
5590332     patrick       davey      <NA>         NaN   

                    primary_email  \
954085   patrick.davey@monash.edu   
5590332  patrick.davey@monash.edu   

                                                  keywords external_ids  \
954085   [radiochemistry, inorganic chemistry, bioinorg...          NaN   
5590332                                                NaN          NaN   

        education                                         employment  n_works  \
954085        NaN  [[phd student, monash university, melbourne, ,...        0   
5590332       NaN  [[phd student, monash university, melbourne, v...        1   

        works_source           activation_date          last_update_date  \
954085           NaN  2019-05-09t23:01:02.170z  2019-08-20t03:00:17.844z   
5590332   [crossref]  2018-09-11t10:47:10.997z  2021-02-09t06:21:44.138z   

         n_doi  n_arxiv  n_pmc  n_other_pids  label primary_email_domain  \
954085       0        0      0             0  False           monash.edu   
5590332      1        0      0             0   True           monash.edu   

        other_email_domains url_domains  n_emails  n_urls  n_ids  n_keywords  \
954085                  NaN         NaN      <NA>    <NA>   <NA>           4   
5590332                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   

         n_education  n_employment  
954085          <NA>             1  
5590332         <NA>             1

In [15]:
df['primary_email_domain'].describe()

count        124722
unique        17160
top       gmail.com
freq          26750
Name: primary_email_domain, dtype: object

In [16]:
top_primary_emails = df[['primary_email_domain', 'orcid']]\
                .groupby('primary_email_domain')\
                .count()\
                .sort_values('orcid', ascending=False)
top_primary_emails

orcid
primary_email_domain       
gmail.com             26750
hotmail.com            3801
yahoo.com              2625
163.com                2132
yuhs.ac                1134
...                     ...
imf.csic.es               1
imf.org                   1
imfd.tu-freiberg.de       1
imft.fr                   1
zzuli.edu.cn              1

[17160 rows x 1 columns]

In [17]:
set_top_n(30)
data = [
    go.Bar(
        x=top_primary_emails[:TOP_N].index,
        y=top_primary_emails[:TOP_N]['orcid']
    )
]

layout = go.Layout(
    title='Top-%s email domains' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

## Other emails

In [18]:
df[df.other_email_domains.notna()].head()

orcid  verified_email  verified_primary_email  \
251  0000-0002-5916-446X            True                    True   
316  0000-0002-8742-947X            True                    True   
433  0000-0001-9097-2281            True                    True   
497  0000-0002-8614-3007            True                    True   
869  0000-0001-9884-5498            True                    True   

        given_names      family_name biography  \
251  antonio gilvan  teixeira júnior      <NA>   
316           aaron  tan shing loong      <NA>   
433        abhishek          solanki      <NA>   
497            adam             arra      <NA>   
869         alberto          ronzani      <NA>   

                                           other_names  \
251  [teixeira, antônio gilvan, júnior, antonio gil...   
316                                                NaN   
433                                                NaN   
497                                                NaN   
869                                                NaN   

                         primary_email  \
251    gilvan.junior@aluno.ufca.edu.br   
316  aaron.tanshingloong@wadh.ox.ac.uk   
433                               <NA>   
497                               <NA>   
869                 alberto@aronza.com   

                                              keywords  \
251  [ethicis; medicine; infectology; neurology; ne...   
316                                                NaN   
433                                                NaN   
497                                                NaN   
869                                                NaN   

                                          external_ids  \
251  [[scopus author id, 56647743200], [scopus auth...   
316                                                NaN   
433                                                NaN   
497                                                NaN   
869                                                NaN   

                                             education  \
251  [[faculty of health and life sciences, , unive...   
316  [[ruskin school of art; wadham college, , univ...   
433                                                NaN   
497                                                NaN   
869                                                NaN   

                                            employment  n_works  \
251                                                NaN       14   
316                                                NaN        0   
433  [[senior engineer, robert bosch (india), benga...        1   
497                                                NaN        0   
869  [[research scientist, vtt technical research c...       19   

                                          works_source  \
251  [antonio gilvan teixeira júnior, scopus - else...   
316                                                NaN   
433                                 [abhishek solanki]   
497                                                NaN   
869  [crossref metadata search, alberto ronzani, cr...   

              activation_date          last_update_date  n_doi  n_arxiv  \
251  2016-05-18t11:26:36.642z  2016-09-20t18:25:05.728z     13        0   
316  2015-10-05t23:10:08.771z  2016-06-14t19:55:50.313z      0        0   
433  2019-04-22t04:43:06.232z  2020-07-02t14:18:28.305z      0        0   
497  2017-11-15t06:33:45.625z  2017-11-15t06:44:02.998z      0        0   
869  2014-04-16t13:21:54.287z  2020-09-28t15:10:37.439z     18        0   

     n_pmc  n_other_pids  label primary_email_domain other_email_domains  \
251      0             8  False    aluno.ufca.edu.br   [liverpool.ac.uk]   
316      0             0  False        wadh.ox.ac.uk      [rsa.ox.ac.uk]   
433      0             0  False                  NaN      [in.bosch.com]   
497      0             0  False                  NaN         [hct.ac.ae]   
869      0             3   True           aronza.com            [vtt.fi]   



In [19]:
emails_by_orcid = df[['orcid', 'n_emails']].sort_values('n_emails', ascending=False)

In [20]:
set_top_n(30)
data = [
    go.Bar(
        x=emails_by_orcid[:TOP_N]['orcid'],
        y=emails_by_orcid[:TOP_N]['n_emails']
    )
]

layout = go.Layout(
    title='Top %s ORCID iDs by email' % TOP_N, 
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [21]:
top_other_emails = df[['orcid', 'other_email_domains']]\
                        .explode('other_email_domains')\
                        .reset_index(drop=True)\
                        .groupby('other_email_domains')\
                        .count()\
                        .sort_values('orcid', ascending=False)

In [22]:
set_top_n(30)
data = [
    go.Bar(
        x=top_other_emails[:TOP_N].index,
        y=top_other_emails[:TOP_N]['orcid']
    )
]

layout = go.Layout(
    title='Top %s other email domains' % TOP_N, 
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

This somehow makes sense, legitimate users could put the gmail account as primary for login purposes and have institutional addresses as other email addresses. It makes also the life easier upon relocation.

## Email speculation

In [23]:
df[df.primary_email.isna() & df.other_email_domains.notna()]

orcid  verified_email  verified_primary_email  \
433       0000-0001-9097-2281            True                    True   
497       0000-0002-8614-3007            True                    True   
898       0000-0003-3728-6439            True                    True   
1719      0000-0001-8330-7443            True                    True   
6829      0000-0001-9670-515X            True                    True   
...                       ...             ...                     ...   
10985816  0000-0003-1204-6009            True                    True   
10986027  0000-0002-3472-7668            True                    True   
10987501  0000-0002-9602-0529            True                    True   
10987829  0000-0003-4402-5982            True                    True   
10988444  0000-0002-1734-7241            True                    True   

             given_names          family_name  \
433             abhishek              solanki   
497                 adam                 arra   
898            alejandra  echeverry velásquez   
1719              andrea            tesoniero   
6829           esma esin             yildirim   
...                  ...                  ...   
10985816          nathan                 walk   
10986027             raf           vandevelde   
10987501  carlos augusto              finelli   
10987829          filipe    de almeida araújo   
10988444     manareldeen                ahmed   

                                                  biography other_names  \
433                                                    <NA>         NaN   
497                                                    <NA>         NaN   
898       alejandra echeverry is an industrial electrici...         NaN   
1719                                                   <NA>         NaN   
6829                                                   <NA>         NaN   
...                                                     ...         ...   
10985816                                               <NA>         NaN   
10986027                                               <NA>         NaN   
10987501                                               <NA>         NaN   
10987829                                               <NA>         NaN   
10988444                                               <NA>         NaN   

         primary_email                                           keywords  \
433               <NA>                                                NaN   
497               <NA>                                                NaN   
898               <NA>  [control, technology, science, innovation, eng...   
1719              <NA>                                                NaN   
6829              <NA>  [pharmacognosy, natural chemistry, chemical en...   
...                ...                                                ...   
10985816          <NA>                                                NaN   
10986027          <NA>                                                NaN   
10987501          <NA>                                                NaN   
10987829          <NA>                                                NaN   
10988444          <NA>  [deep learning, atomistic simulation, graphene...   

                           external_ids  \
433                                 NaN   
497                                 NaN   
898                                 NaN   
1719      [[researcherid, d-9056-2015]]   
6829                                NaN   
...                                 ...   
10985816                            NaN   
10986027                            NaN   
10987501                            NaN   
10987829                            NaN   
10988444                            NaN   

                                                  education  \
433                                                     NaN   
497                                                     NaN   
898       [[, electrical e

## URLs

In [24]:
df[df.url_domains.notna()].head()

orcid  verified_email  verified_primary_email  \
6    0000-0001-7402-0096            True                    True   
11   0000-0001-8377-3508            True                    True   
29   0000-0002-2638-4108            True                    True   
46   0000-0003-1435-6545            True                    True   
158  0000-0003-1284-9741            True                    True   

            given_names       family_name  \
6                  <NA>              <NA>   
11                 <NA>              <NA>   
29                 <NA>              <NA>   
46                 <NA>              <NA>   
158  alex percy antonio  manriquez paisig   

                                             biography  \
6                                                 <NA>   
11                                                <NA>   
29   investigador de la universidad de oviedo. depa...   
46                                                <NA>   
158                                               <NA>   

                    other_names primary_email  \
6                           NaN          <NA>   
11   [fontana, milena da silva]          <NA>   
29                          NaN          <NA>   
46                          NaN          <NA>   
158                         NaN          <NA>   

                                              keywords  \
6                                                  NaN   
11                [educação; informática; matemática.]   
29   [constitutional history, history of political ...   
46          [prostate cancer, migration, culture cell]   
158                                                NaN   

                          external_ids  \
6                                  NaN   
11                                 NaN   
29   [[scopus author id, 54394231000]]   
46       [[researcherid, p-2223-2018]]   
158                                NaN   

                                             education  \
6                                                  NaN   
11                                                 NaN   
29   [[public law, ph doctor, university of oviedo,...   
46   [[morfologia, , universidade estadual paulista...   
158                                                NaN   

                                            employment  n_works works_source  \
6    [[, kth royal institute of technology, stockho...        0          NaN   
11   [[, instituto federal de educação, ciência e t...        0          NaN   
29   [[professor of constitutional law, university ...        1   [crossref]   
46   [[, universidade estadual paulista (unesp), in...        0          NaN   
158                                                NaN        0          NaN   

              activation_date          last_update_date  n_doi  n_arxiv  \
6    2015-01-11t15:13:06.467z  2016-06-14t23:55:59.896z      0        0   
11   2018-05-23t23:39:04.534z  2019-10-16t02:50:11.007z      0        0   
29   2013-03-25t14:38:06.016z  2020-07-01t13:10:37.025z      1        0   
46   2018-08-09t12:12:24.405z  2020-04-22t01:38:03.184z      0        0   
158  2020-09-08t20:04:33.906z  2020-09-08t20:25:55.432z      0        0   

     n_pmc  n_other_pids  label primary_email_domain other_email_domains  \
6        0             0  False                  NaN                 NaN   
11       0             0  False                  NaN                 NaN   
29       0             0  False                  NaN                 NaN   
46       0             0  False                  NaN                 NaN   
158      0             0  False                  NaN                 NaN   

                 url_domains  n_emails  n_urls  n_ids  n_keywords  \
6                   [kth.se]      <NA>       1   <NA>        <NA>   
11                 [cnpq.br]      <NA>       1   <NA>           1   
29            [unioviedo.es]      <NA>       1      1           3   
46   [cnpq.br, linkedin.com]      <NA>       2      1           3   
158       

In [25]:
urls_by_orcid = df[['orcid', 'n_urls']].sort_values('n_urls', ascending=False)
urls_by_orcid

orcid  n_urls
3226518   0000-0002-1234-835X     219
4206055   0000-0001-7478-4539     174
4901870   0000-0002-7392-3792     169
8184260   0000-0002-6938-9638     152
2743648   0000-0002-5710-4041     114
...                       ...     ...
10989644  0000-0002-1686-1935    <NA>
10989645  0000-0002-3800-6331    <NA>
10989646  0000-0002-8783-5814    <NA>
10989647  0000-0002-7584-2283    <NA>
10989648  0000-0003-0529-3538    <NA>

[10989649 rows x 2 columns]

In [26]:
set_top_n(100)
data = [
    go.Bar(
        x=urls_by_orcid[:TOP_N]['orcid'],
        y=urls_by_orcid[:TOP_N]['n_urls']
    )
]

layout = go.Layout(
    title='Top %s ORCID iDs with URLs' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [27]:
top_urls = df[['orcid', 'url_domains']]\
                .explode('url_domains')\
                .reset_index(drop=True)\
                .groupby('url_domains')\
                .count()\
                .sort_values('orcid', ascending=False)

In [28]:
set_top_n(50)
data = [
    go.Bar(
        x=top_urls[:TOP_N].index,
        y=top_urls[:TOP_N]['orcid']
    )
]

layout = go.Layout(
    title='Top-%s URL domains' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

## URLs speculation

In [29]:
df[(df['url_domains'].str.len() > 50) & (df['n_works'] > 0)]

orcid  verified_email  verified_primary_email  \
1025713   0000-0003-2407-3557            True                    True   
2743648   0000-0002-5710-4041            True                    True   
3011724   0000-0003-2450-090X            True                    True   
3881064   0000-0002-3920-7389            True                    True   
7466062   0000-0002-1929-6054            True                    True   
7517096   0000-0003-4948-9268            True                    True   
8068275   0000-0003-2183-8112            True                    True   
8184260   0000-0002-6938-9638            True                    True   
8791256   0000-0002-9025-8632            True                    True   
10174509  0000-0002-9965-2425            True                    True   
10257808  0000-0002-4062-3603            True                    True   
10486212  0000-0002-3997-5070            True                    True   
10652632  0000-0003-2593-7134            True                    True   

                 given_names        family_name  \
1025713                abdul               aziz   
2743648              ryszard           romaniuk   
3011724               eduard            babulak   
3881064                   а.              гусев   
7466062     franklin américo      canaza choque   
7517096             gustavo             duperré   
8068275        pelayo munhoz               olea   
8184260               adolfo    catral sanabria   
8791256          buycannabis         dispensary   
10174509            jaroslaw           spychala   
10257808       juan de dios   beltrán mancilla    
10486212  dr. parameshachari                b d   
10652632                 aan            jaelani   

                                                  biography  \
1025713   abdul aziz was born on may 25, 1973, in brebes...   
2743648   professor of electronics and communications en...   
3011724   professor eduard babulak is accomplished inter...   
3881064   surname, name gusev  alexander leonidovichdate...   
7466062   docente-investigador social. maestrando en der...   
7517096   gustavo norberto duperré graduated in arts and...   
8068275   pós-doutorado em gestão ambiental pela univers...   
8184260   my education is in computer science, mathemati...   
8791256   we procure and deliver premium cannabis strain...   
10174509  jaroslaw spychala has received a doctoral degr...   
10257808  juan de dios beltrán mancilla (*) filósofo aut...   
10486212  dr. parameshachari b dacm distinguished speake...   
10652632  all my papers can be downloaded from portal:re...   

                                                other_names  \
1025713   [abdul aziz, aziz, abdul, aziz, a., aziz, abd,...   
2743648   [r.romaniuk, r.s.romaniuk, ryszard romaniuk, r...   
3011724                          [professor eduard babulak]   
3881064   [alexander l. gusev , alexander leonidovich gu...   
7466062   [franklin américo canaza-choque , franklin a. ...   
7517096   [gustavo norberto duperré, duperré, g. n., gus...   
8068275   [ munhoz, pelayo olea,  olea, pelayo,  olea, p...   
8184260                                                 NaN   
8791256   [we procure and deliver premium cannabis strai...   
10174509                          [jaroslaw jozef spychala]   
10257808  [juan de dios beltrán mancilla, filósofo autod...   
10486212                           [dr. parameshachari b d]   
10652632                        [jaelani, a., jaelani, aan]   

                           primary_email  \
1025713                             <NA>   
2743648               rrom@ise.pw.edu.pl   
3011724                             <NA>   
3881064                             <NA>   
7466062            leo_123fa@hotmail.com   
7517096      gustavo.duperre@usal.edu.ar   
8068275                             <NA>   
8184260                             <NA>   
8791256                             <NA>   
10174509                            <NA>   
10257808                            

In [30]:
df[(df['url_domains'].str.len() > 10) & (df['n_works'] > 0) & (df['works_source'].str.len() == 1)]

orcid  verified_email  verified_primary_email  \
47439     0000-0002-5967-2835            True                    True   
72557     0000-0002-3505-2797            True                    True   
94081     0000-0003-3670-9620            True                    True   
261673    0000-0002-5441-0465            True                    True   
326211    0000-0002-7781-6767            True                    True   
...                       ...             ...                     ...   
10579801  0000-0001-5087-6965            True                    True   
10590882  0000-0002-3318-9861            True                    True   
10766062  0000-0001-8960-9004            True                    True   
10807839  0000-0002-4379-6454            True                    True   
10911966  0000-0003-2311-0600            True                    True   

               given_names     family_name  \
47439              oleksiy      goryayinov   
72557                nurul      malahayati   
94081               carlos         barrera   
261673               nuria  hernández-león   
326211          mohd nazri          ismail   
...                    ...             ...   
10579801            robert           ohara   
10590882          shagufta         perveen   
10766062             susan         bastani   
10807839  caroline wanjiru         kariuki   
10911966               myo     kyaw hlaing   

                                                  biography  \
47439                                                  <NA>   
72557                                        google scholar   
94081     im individual inventor, and this is my work; s...   
261673                                                 <NA>   
326211    born in penang, malaysia in 1971, dr. mohd had...   
...                                                     ...   
10579801  systematics, evolutionary biology, and the his...   
10590882  prof. dr. shagufta perveen is a professor at k...   
10766062                                               <NA>   
10807839  caroline holds a phd in economics from curtin ...   
10911966                                               <NA>   

                                                other_names  \
47439     [алексей николаевич горяинов, о.м.горяїнов, а....   
72557                                                   NaN   
94081                           [retrodynamic, novelinflow]   
261673    [nuria h. león, nuria hernández león, hernánde...   
326211     [ndum (national defence university of malaysia)]   
...                                                     ...   
10579801  [r. o’hara, r.j. o’hara, robert o’hara, robert...   
10590882                                                NaN   
10766062                         [s. bastani, سوسن باستانی]   
10807839                                                NaN   
10911966                               [dr myo kyaw hlaing]   

                     primary_email  \
47439                         <NA>   
72557                         <NA>   
94081                         <NA>   
261673                        <NA>   
326211                        <NA>   
...                            ...   
10579801                      <NA>   
10590882  shagufta792000@yahoo.com   
10766062    sbastani@alzahra.ac.ir   
10807839                      <NA>   
10911966                      <NA>   

                                                   keywords  \
47439                   [diagnostics, transport, logistics]   
72557                                                   NaN   
94081     [energy, technology, gearturbine, imploturboco...   
261673    [training, icts, business management, research...   
326211    [wsn, manet, simulation and modelling, network...   
...                                                     ...   
10579801  [history and philosophy of science, evolutiona...   
10590882  [shagufta perveen professor, shagufta perveen ...   
10766062  [social networks, fuzzy logic, online and offl

In [31]:
exploded_sources = df[(df['url_domains'].str.len() > 10) & (df['n_works'] > 0) & (df['works_source'].str.len() == 1)].explode('works_source').reset_index(drop=True)
exploded_sources

orcid  verified_email  verified_primary_email  \
0    0000-0002-5967-2835            True                    True   
1    0000-0002-3505-2797            True                    True   
2    0000-0003-3670-9620            True                    True   
3    0000-0002-5441-0465            True                    True   
4    0000-0002-7781-6767            True                    True   
..                   ...             ...                     ...   
135  0000-0001-5087-6965            True                    True   
136  0000-0002-3318-9861            True                    True   
137  0000-0001-8960-9004            True                    True   
138  0000-0002-4379-6454            True                    True   
139  0000-0003-2311-0600            True                    True   

          given_names     family_name  \
0             oleksiy      goryayinov   
1               nurul      malahayati   
2              carlos         barrera   
3               nuria  hernández-león   
4          mohd nazri          ismail   
..                ...             ...   
135            robert           ohara   
136          shagufta         perveen   
137             susan         bastani   
138  caroline wanjiru         kariuki   
139               myo     kyaw hlaing   

                                             biography  \
0                                                 <NA>   
1                                       google scholar   
2    im individual inventor, and this is my work; s...   
3                                                 <NA>   
4    born in penang, malaysia in 1971, dr. mohd had...   
..                                                 ...   
135  systematics, evolutionary biology, and the his...   
136  prof. dr. shagufta perveen is a professor at k...   
137                                               <NA>   
138  caroline holds a phd in economics from curtin ...   
139                                               <NA>   

                                           other_names  \
0    [алексей николаевич горяинов, о.м.горяїнов, а....   
1                                                  NaN   
2                          [retrodynamic, novelinflow]   
3    [nuria h. león, nuria hernández león, hernánde...   
4     [ndum (national defence university of malaysia)]   
..                                                 ...   
135  [r. o’hara, r.j. o’hara, robert o’hara, robert...   
136                                                NaN   
137                         [s. bastani, سوسن باستانی]   
138                                                NaN   
139                               [dr myo kyaw hlaing]   

                primary_email  \
0                        <NA>   
1                        <NA>   
2                        <NA>   
3                        <NA>   
4                        <NA>   
..                        ...   
135                      <NA>   
136  shagufta792000@yahoo.com   
137    sbastani@alzahra.ac.ir   
138                      <NA>   
139                      <NA>   

                                              keywords  \
0                  [diagnostics, transport, logistics]   
1                                                  NaN   
2    [energy, technology, gearturbine, imploturboco...   
3    [training, icts, business management, research...   
4    [wsn, manet, simulation and modelling, network...   
..                                                 ...   
135  [history and philosophy of science, evolutiona...   
136  [shagufta perveen professor, shagufta perveen ...   
137  [social networks, fuzzy logic, online and offl...   
138  [development economics, applied econometrics, ...   
139                                 [economic geology]   

                                          external_ids  \
0                        [[researcherid, i-7977-2016]]   
1                        [[researcherid, q-3861-2017]]   
2                             [[loop profile, 3

In [32]:
exploded_sources[exploded_sources.apply(lambda x: x['works_source'].find(x['given_names']) >= 0, axis=1)]

orcid  verified_email  verified_primary_email  \
0    0000-0002-5967-2835            True                    True   
1    0000-0002-3505-2797            True                    True   
2    0000-0003-3670-9620            True                    True   
3    0000-0002-5441-0465            True                    True   
5    0000-0001-7010-2908            True                    True   
..                   ...             ...                     ...   
133  0000-0003-1020-1351            True                    True   
134  0000-0001-7228-5680            True                    True   
135  0000-0001-5087-6965            True                    True   
138  0000-0002-4379-6454            True                    True   
139  0000-0003-2311-0600            True                    True   

          given_names     family_name  \
0             oleksiy      goryayinov   
1               nurul      malahayati   
2              carlos         barrera   
3               nuria  hernández-león   
5               clara        sarmento   
..                ...             ...   
133  sheikh saifullah           ahmed   
134              text        protocol   
135            robert           ohara   
138  caroline wanjiru         kariuki   
139               myo     kyaw hlaing   

                                             biography  \
0                                                 <NA>   
1                                       google scholar   
2    im individual inventor, and this is my work; s...   
3                                                 <NA>   
5    clara sarmento holds an aggregation in cultura...   
..                                                 ...   
133  sheikh saifullah ahmed is a full-time lecturer...   
134                                               <NA>   
135  systematics, evolutionary biology, and the his...   
138  caroline holds a phd in economics from curtin ...   
139                                               <NA>   

                                           other_names  \
0    [алексей николаевич горяинов, о.м.горяїнов, а....   
1                                                  NaN   
2                          [retrodynamic, novelinflow]   
3    [nuria h. león, nuria hernández león, hernánde...   
5                                                  NaN   
..                                                 ...   
133                                                NaN   
134                                                NaN   
135  [r. o’hara, r.j. o’hara, robert o’hara, robert...   
138                                                NaN   
139                               [dr myo kyaw hlaing]   

                  primary_email  \
0                          <NA>   
1                          <NA>   
2                          <NA>   
3                          <NA>   
5                          <NA>   
..                          ...   
133  saifullahahmedku@gmail.com   
134                        <NA>   
135                        <NA>   
138                        <NA>   
139                        <NA>   

                                              keywords  \
0                  [diagnostics, transport, logistics]   
1                                                  NaN   
2    [energy, technology, gearturbine, imploturboco...   
3    [training, icts, business management, research...   
5    [portuguese culture and literature, cultural a...   
..                                                 ...   
133  [south asian literature, postmodern literature...   
134                                                NaN   
135  [history and philosophy of science, evolutiona...   
138  [development economics, applied econometrics, ...   
139                                 [economic geology]   

                                          external_ids  \
0                        [[researcherid, i-7977-2016]]   
1                        [[researcherid, q-3861-2017]]   
2                      

## Works source

In [33]:
def remove_own_source(lst, given, family):
    res = []
    for ws in lst:
        if ws.lower().find(given.lower()) == -1:
            if pd.notna(family):
                if ws.lower().find(family.lower()) == -1:
                    res.append(ws)
            else:
                res.append(ws)
    return res

In [34]:
df['ext_works_source'] = df[(df.works_source.notna()) & (df.given_names.notna())]\
                        .apply(lambda x: remove_own_source(x['works_source'], x['given_names'], x['family_name']), axis=1)

In [35]:
df['n_ext_work_source'] = df.ext_works_source.str.len()

In [36]:
exploded_external_sources = df[df['ext_works_source'].str.len() > 0][['orcid','ext_works_source']]\
                            .explode('ext_works_source').reset_index(drop=True)

In [37]:
grouped_ext_sources = exploded_external_sources.groupby('ext_works_source')\
                        .count()\
                        .sort_values('orcid', ascending=False)\
                        .reset_index()

In [38]:
data = [
    go.Bar(
        x=grouped_ext_sources[:30].ext_works_source,
        y=grouped_ext_sources[:30].orcid
    )
]

layout = go.Layout(
    title='Top 30 works_source',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [39]:
authoritative_sources = grouped_ext_sources[grouped_ext_sources['orcid'] > 2]
authoritative_sources

ext_works_source    orcid
0                                          crossref  1460841
1                                 scopus - elsevier   902231
2                          crossref metadata search   297684
3    multidisciplinary digital publishing institute   281664
4                             europe pubmed central   181605
..                                              ...      ...
337                 uta - oa journal global insight        3
338                        francis crick institute         3
339                                            anna        3
340                                          santos        3
341          universitäts- und stadtbibliothek köln        3

[342 rows x 2 columns]

In [40]:
exploded_external_sources['authoritative'] = exploded_external_sources.ext_works_source\
                                            .isin(authoritative_sources['ext_works_source'])

In [41]:
orcid_authoritative_source = exploded_external_sources\
                            .groupby('orcid')['authoritative']\
                            .any()\
                            .reset_index()[['orcid', 'authoritative']]

In [42]:
df = df.set_index('orcid').join(orcid_authoritative_source.set_index('orcid')).reset_index()

In [43]:
df.loc[df.authoritative.isna(), 'authoritative'] = False

In [44]:
df.head()

orcid  verified_email  verified_primary_email given_names  \
0  0000-0001-6097-3953           False                   False        <NA>   
1  0000-0001-6112-5550            True                    True        <NA>   
2  0000-0001-6152-2695            True                    True        <NA>   
3  0000-0001-6220-5683            True                    True        <NA>   
4  0000-0001-7071-8294            True                    True        <NA>   

  family_name biography                 other_names primary_email keywords  \
0        <NA>      <NA>                         NaN          <NA>      NaN   
1        <NA>      <NA>  [v.i. yurtaev; v. yurtaev]          <NA>      NaN   
2        <NA>      <NA>                         NaN          <NA>      NaN   
3        <NA>      <NA>                         NaN          <NA>      NaN   
4        <NA>      <NA>                         NaN          <NA>      NaN   

  external_ids education                                         employment  \
0          NaN       NaN                                                NaN   
1          NaN       NaN  [[professor, peoples friendship university of ...   
2          NaN       NaN                                                NaN   
3          NaN       NaN  [[research scientist, new york university abu ...   
4          NaN       NaN  [[researcher (academic), universidad de zarago...   

   n_works works_source           activation_date          last_update_date  \
0        0          NaN  2018-03-02t09:29:16.528z  2018-03-02t09:43:07.551z   
1        0          NaN  2018-04-03t07:50:23.358z  2020-03-18t09:42:44.753z   
2        0          NaN  2019-12-11t15:31:56.388z  2020-01-28t15:34:17.309z   
3        0          NaN  2015-08-18t12:36:45.307z  2020-09-23t13:37:54.180z   
4        0          NaN  2014-03-10t13:22:01.966z  2016-06-14t22:17:54.470z   

   n_doi  n_arxiv  n_pmc  n_other_pids  label primary_email_domain  \
0      0        0      0             0  False                  NaN   
1      0        0      0             0  False                  NaN   
2      0        0      0             0  False                  NaN   
3      0        0      0             0  False                  NaN   
4      0        0      0             0  False                  NaN   

  other_email_domains url_domains  n_emails  n_urls  n_ids  n_keywords  \
0                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   
1                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   
2                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   
3                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   
4                 NaN         NaN      <NA>    <NA>   <NA>        <NA>   

   n_education  n_employment ext_works_source  n_ext_work_source authoritative  
0         <NA>          <NA>              NaN                NaN         False  
1         <NA>             1              NaN                NaN         False  
2         <NA>          <NA>              NaN                NaN         False  
3         <NA>             1              NaN                NaN         False  
4         <NA>             2              NaN                NaN         False

## External IDs

External IDs should come from reliable sources. ORCiD registrants cannot add them freely.

In [45]:
df.n_ids.describe()

count    1.308598e+06
mean     1.359082e+00
std      6.643235e-01
min      1.000000e+00
25%      1.000000e+00
50%      1.000000e+00
75%      2.000000e+00
max      8.000000e+01
Name: n_ids, dtype: float64

In [46]:
df[df.n_ids == df.n_ids.max()]

orcid  verified_email  verified_primary_email  \
3896226  0000-0002-9554-6633            True                    True   

        given_names family_name biography other_names primary_email keywords  \
3896226      john a    williams      <NA>         NaN          <NA>      NaN   

                                              external_ids education  \
3896226  [[scopus author id,  55553733518], [scopus aut...       NaN   

                                                employment  n_works  \
3896226  [[, aston university, birmingham, , gb, 1722, ...       92   

                      works_source           activation_date  \
3896226  [aston research explorer]  2014-11-20t09:42:10.690z   

                 last_update_date  n_doi  n_arxiv  n_pmc  n_other_pids  label  \
3896226  2021-03-17t01:00:51.203z     80        0      0           208   True   

        primary_email_domain other_email_domains    url_domains  n_emails  \
3896226                  NaN                 NaN  [aston.ac.uk]      <NA>   

         n_urls  n_ids  n_keywords  n_education  n_employment  \
3896226       1     80        <NA>         <NA>             1   

                  ext_works_source  n_ext_work_source authoritative  
3896226  [aston research explorer]                1.0          True

In [47]:
ids = df[['orcid', 'external_ids']].explode('external_ids').reset_index(drop=True)

In [48]:
ids['provider'] = ids[ids.external_ids.notna()]['external_ids'].apply(lambda x: x[0])

In [49]:
ids[ids.provider.notna()].head()

orcid                     external_ids          provider
9   0000-0001-8315-2066      [researcherid, k-4630-2014]      researcherid
29  0000-0002-2638-4108  [scopus author id, 54394231000]  scopus author id
46  0000-0003-1435-6545      [researcherid, p-2223-2018]      researcherid
50  0000-0003-2259-7023  [scopus author id, 57189297461]  scopus author id
64  0000-0002-7397-5824   [scopus author id, 8399842800]  scopus author id

In [50]:
top_ids_providers = ids.groupby('provider').count().sort_values('orcid', ascending=False)

In [51]:
data = [
    go.Bar(
        x=top_ids_providers.index,
        y=top_ids_providers['orcid']
    )
]

layout = go.Layout(
    title='IDs provided by providers',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [52]:
pd.unique(ids['provider'])

array([nan, 'researcherid', 'scopus author id', 'loop profile', 'gnd',
       'ciência id', 'researcher name resolver id', 'pitt id',
       'id dialnet', 'isni', 'technical university of denmark cwis',
       'chalmers id', 'scopus author id: ', 'scopus author id:',
       'hkust profile', 'hku researcherpage', '中国科学家在线', 'uow scholars',
       'sciprofile', 'cti vitae', 'digital author id', 'researcher id',
       'authenticusid', 'authid', 'authenticus', 'scopus  id',
       'digital author id (dai)', 'researcherid:', 'vivo cornell',
       'us epa vivo', 'escientist', 'github', 'iauthor', 'orcid id',
       'dai', 'scopus id', 'smithsonian profiles', 'google scholar',
       'kaken', 'dialnet id', 'researcherid: ', 'une researcher id',
       'sciprofiles', 'id dialnet:', 'scienceopen', 'orcid',
       'profile system identifier', 'custom'], dtype=object)

## Keywords

This field is problematic as users can be nasty and put multiple keywords in one as opposed of having different keywords. Look this

In [53]:
keywords_by_orcid = df[['orcid', 'n_keywords']].sort_values('n_keywords', ascending=False)
keywords_by_orcid

orcid  n_keywords
3751714   0000-0002-0673-0341         154
8697926   0000-0003-3343-5660         148
1154523   0000-0002-6075-3501         140
6512971   0000-0002-7060-4112         140
1515197   0000-0001-5287-1949         132
...                       ...         ...
10989644  0000-0002-1686-1935        <NA>
10989645  0000-0002-3800-6331        <NA>
10989646  0000-0002-8783-5814        <NA>
10989647  0000-0002-7584-2283        <NA>
10989648  0000-0003-0529-3538        <NA>

[10989649 rows x 2 columns]

In [54]:
set_top_n(100)
data = [
    go.Bar(
        x=keywords_by_orcid[:TOP_N]['orcid'],
        y=keywords_by_orcid[:TOP_N]['n_keywords']
    )
]

layout = go.Layout(
    title='Keywords provided by ORCiD',
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [55]:
top_keywords = df[['orcid', 'keywords']]\
                .explode('keywords')\
                .reset_index(drop=True)\
                .groupby('keywords')\
                .count()\
                .sort_values('orcid', ascending=False)

In [56]:
set_top_n(50)
data = [
    go.Bar(
        x=top_keywords[:TOP_N].index,
        y=top_keywords[:TOP_N]['orcid']
    )
]

layout = go.Layout(
    title='Top-%s keywords occurrence' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

## Education

In [120]:
df.n_education.describe()

count    1.753340e+06
mean     1.913072e+00
std      1.197388e+00
min      1.000000e+00
25%      1.000000e+00
50%      2.000000e+00
75%      3.000000e+00
max      2.000000e+02
Name: n_education, dtype: float64

In [121]:
df[df.n_education == df.n_education.max()]

orcid  verified_email  verified_primary_email  \
2568539  0000-0002-1927-0292            True                    True   

           given_names     family_name  \
2568539  phd. carmen m  galvez-sánchez   

                                                 biography other_names  \
2568539  my name is carmen maria galvez sánchez. i´m a ...         NaN   

        primary_email                                           keywords  \
2568539          <NA>  [qualitative research, fibromyalgia, quantitat...   

                                              external_ids  \
2568539  [[loop profile, 509331], [scopus author id, 57...   

                                                 education  \
2568539  [[psychology, 2019-2020 course. degree in psyc...   

                                                employment  n_works  \
2568539  [[researcher and teaching staff. postdoctoral ...       35   

                                              works_source  \
2568539  [phd. carmen m galvez-sánchez, multidisciplina...   

                  activation_date          last_update_date  n_doi  n_arxiv  \
2568539  2016-04-18t14:28:57.237z  2021-03-06t14:17:33.246z     24        0   

         n_pmc  n_other_pids  label primary_email_domain other_email_domains  \
2568539      0             7   True                  NaN                 NaN   

        url_domains  n_emails  n_urls  n_ids  n_keywords  n_education  \
2568539         NaN      <NA>    <NA>      2           5          200   

         n_employment                                   ext_works_source  \
2568539             3  [multidisciplinary digital publishing institut...   

         n_ext_work_source authoritative  spam_score  n_valid_employment  
2568539                4.0          True    0.999948                   1

In [57]:
exploded_education = df[['orcid', 'education']].explode('education').dropna()
exploded_education

orcid  \
28        0000-0002-2343-910X   
28        0000-0002-2343-910X   
28        0000-0002-2343-910X   
29        0000-0002-2638-4108   
46        0000-0003-1435-6545   
...                       ...   
10989644  0000-0002-1686-1935   
10989645  0000-0002-3800-6331   
10989645  0000-0002-3800-6331   
10989647  0000-0002-7584-2283   
10989647  0000-0002-7584-2283   

                                                  education  
28        [aeronautics and astronautics, phd, massachuse...  
28        [aeronautics and astronautics, sm, massachuset...  
28        [mechanical engineering and material science, ...  
29        [public law, ph doctor, university of oviedo, ...  
46        [morfologia, , universidade estadual paulista ...  
...                                                     ...  
10989644  [, , south china agricultural university, guan...  
10989645  [richard gilder graduate school, phd in compar...  
10989645  [geological sciences and history (dual major),...  
10989647  [school of electronics and information, master...  
10989647  [ department of electrical engineering, bachel...  

[4434439 rows x 2 columns]

In [58]:
exploded_education[['degree', 'role', 'university', 'city', 'region', 'country', 'id', 'id_scheme']] = pd.DataFrame(exploded_education.education.tolist(), index=exploded_education.index)

In [130]:
exploded_education.id.replace('', pd.NA, inplace=True)

In [132]:
exploded_education.groupby('orcid').id.count().reset_index()

orcid  id
0        0000-0001-5000-0162   3
1        0000-0001-5000-0170   2
2        0000-0001-5000-0218   3
3        0000-0001-5000-0226   1
4        0000-0001-5000-0306   0
...                      ...  ..
2441640  0000-0003-4999-9719   1
2441641  0000-0003-4999-9735   1
2441642  0000-0003-4999-992X   2
2441643  0000-0003-4999-9938   2
2441644  0000-0003-4999-9954   1

[2441645 rows x 2 columns]

In [133]:
df = df.merge(exploded_education.groupby('orcid').id.count().reset_index(), on='orcid')
df.rename(columns={'id': 'n_valid_education'}, inplace=True)

In [134]:
df[df.n_education != df.n_valid_education]

orcid  verified_email  verified_primary_email  \
2        0000-0003-1435-6545            True                    True   
6        0000-0002-0427-9745            True                    True   
9        0000-0002-3380-6671            True                    True   
11       0000-0001-6902-6549            True                    True   
12       0000-0002-6142-6406            True                    True   
...                      ...             ...                     ...   
1753316  0000-0002-1842-4130            True                    True   
1753319  0000-0003-0459-4822            True                    True   
1753320  0000-0003-0057-1551            True                    True   
1753325  0000-0003-4653-4705            True                    True   
1753337  0000-0002-1686-1935            True                    True   

           given_names       family_name  \
2                 <NA>              <NA>   
6               a. can              inci   
9                abdul         asis pata   
11            abubakar          muhammad   
12                adam           mamadou   
...                ...               ...   
1753316  josé de jesús  cázares-marinero   
1753319          luana              <NA>   
1753320       lyudmyla         antypenko   
1753325       patricia          teixeira   
1753337         youxia              wang   

                                                 biography  \
2                                                     <NA>   
6        i am a professor of finance at bryant universi...   
9                                                     <NA>   
11                                                    <NA>   
12                                                    <NA>   
...                                                    ...   
1753316                                               <NA>   
1753319  mestranda em tecnologia na saúde e foi aluna o...   
1753320  the phd degree of pharmacy was received under ...   
1753325  2005 - phd, university of coimbrajuly 2009-jun...   
1753337  youxia wang (1995-), native of zunyi, guizhou ...   

                                               other_names primary_email  \
2                                                      NaN          <NA>   
6                                                      NaN          <NA>   
9                                                      NaN          <NA>   
11                                                     NaN          <NA>   
12                                                     NaN          <NA>   
...                                                    ...           ...   
1753316                                     [josé cázares]          <NA>   
1753319                               [luana bastos morey]          <NA>   
1753320  [lyudmila nikolaevna antipenko (russian transl...          <NA>   
1753325                                                NaN          <NA>   
1753337                                                NaN          <NA>   

                                                  keywords  \
2               [prostate cancer, migration, culture cell]   
6                                                      NaN   
9                                                      NaN   
11                                                     NaN   
12                                                     NaN   
...                                                    ...   
1753316  [chemical biology, industrial chemistry, biote...   
1753319  [tradução; língua espanhol; língua portuguesa;...   
1753320  [pharmaceutical chemistry, organic synthesis, ...   
1753325  [ecotoxicology, heavy metals, steroid hormones...   
1753337                                                NaN   

                                              external_ids  \
2                            [[researcherid, p-2223-2018]]   
6        [[researcherid, b-5471-2018], [scopus author i...   
9                                       

## Employment

In [116]:
df.n_employment.describe()

count    2.680488e+06
mean     1.664713e+00
std      1.530077e+00
min      1.000000e+00
25%      1.000000e+00
50%      1.000000e+00
75%      2.000000e+00
max      1.980000e+02
Name: n_employment, dtype: float64

In [119]:
df[df.n_employment == df.n_employment.max()]

orcid  verified_email  verified_primary_email  \
2020738  0000-0002-0293-964X            True                    True   

        given_names family_name biography other_names    primary_email  \
2020738   ben zhong        tang      <NA>       [唐本忠]  tangbenz@ust.hk   

                                                  keywords  \
2020738  [fluorescent biosensors, light-emitting molecu...   

                                              external_ids  \
2020738  [[hkust profile, tang-benzhong], [researcherid...   

                                                 education  \
2020738  [[department of chemistry and faculty of pharm...   

                                                employment  n_works  \
2020738  [[chair professor, division of biomedical engi...      422   

                       works_source           activation_date  \
2020738  [tang, benzhong, crossref]  2015-03-13t00:28:33.270z   

                 last_update_date  n_doi  n_arxiv  n_pmc  n_other_pids  label  \
2020738  2021-03-23t07:56:34.824z    359        0      0             0  False   

        primary_email_domain other_email_domains url_domains  n_emails  \
2020738               ust.hk                 NaN    [ust.hk]      <NA>   

         n_urls  n_ids  n_keywords  n_education  n_employment  \
2020738       1      3           7            7           198   

        ext_works_source  n_ext_work_source authoritative  spam_score  \
2020738       [crossref]                1.0          True         NaN   

         n_valid_employment  
2020738                  32

Let's count how many employments have a valid assigned id by orcid (ringols, isni, grid, etc.)

In [60]:
exploded_employment = df[['orcid', 'employment']].explode('employment').dropna()
exploded_employment

orcid  \
1         0000-0001-6112-5550   
3         0000-0001-6220-5683   
4         0000-0001-7071-8294   
4         0000-0001-7071-8294   
6         0000-0001-7402-0096   
...                       ...   
10989643  0000-0003-2606-0936   
10989644  0000-0002-1686-1935   
10989645  0000-0002-3800-6331   
10989645  0000-0002-3800-6331   
10989647  0000-0002-7584-2283   

                                                 employment  
1         [professor, peoples friendship university of r...  
3         [research scientist, new york university abu d...  
4         [researcher (academic), universidad de zaragoz...  
4         [researcher (academic), instituto de síntesis ...  
6         [, kth royal institute of technology, stockhol...  
...                                                     ...  
10989643  [post-doc, institute of biochemistry and cell ...  
10989644  [master, sichuan agricultural university , che...  
10989645  [assistant professor, baruch college, city uni...  
10989645  [postdoctoral scholar, university of californi...  
10989647  [lecturer, henan institute of science and tech...  

[4462243 rows x 2 columns]

In [61]:
exploded_employment[['role', 'institution', 'city', 'region', 'country', 'id', 'id_scheme']] = pd.DataFrame(exploded_employment.employment.tolist(), index=exploded_employment.index)

In [83]:
exploded_employment.id.replace('', pd.NA, inplace=True)

In [105]:
exploded_employment.groupby('orcid').id.count().reset_index()

orcid  id
0        0000-0001-5000-0031   1
1        0000-0001-5000-0138   1
2        0000-0001-5000-0170   2
3        0000-0001-5000-0218   1
4        0000-0001-5000-0226   1
...                      ...  ..
2680483  0000-0003-4999-9831   1
2680484  0000-0003-4999-9890   1
2680485  0000-0003-4999-992X   0
2680486  0000-0003-4999-9938   1
2680487  0000-0003-4999-9954   2

[2680488 rows x 2 columns]

In [106]:
df = df.merge(exploded_employment.groupby('orcid').id.count().reset_index(), on='orcid')
df.rename(columns={'id': 'n_valid_employment'}, inplace=True)

orcid  verified_email  verified_primary_email  \
0        0000-0001-6112-5550            True                    True   
1        0000-0001-6220-5683            True                    True   
2        0000-0001-7071-8294            True                    True   
3        0000-0001-7402-0096            True                    True   
4        0000-0001-8315-2066            True                    True   
...                      ...             ...                     ...   
2680483  0000-0002-8004-688X            True                    True   
2680484  0000-0003-2606-0936            True                    True   
2680485  0000-0002-1686-1935            True                    True   
2680486  0000-0002-3800-6331            True                    True   
2680487  0000-0002-7584-2283            True                    True   

        given_names     family_name  \
0              <NA>            <NA>   
1              <NA>            <NA>   
2              <NA>            <NA>   
3              <NA>            <NA>   
4              <NA>            <NA>   
...             ...             ...   
2680483        paul  wanjala muyoma   
2680484       luang              xu   
2680485      youxia            wang   
2680486     zachary        calamari   
2680487          现刚               左   

                                                 biography  \
0                                                     <NA>   
1                                                     <NA>   
2                                                     <NA>   
3                                                     <NA>   
4                                                     <NA>   
...                                                    ...   
2680483                                               <NA>   
2680484                                               <NA>   
2680485  youxia wang (1995-), native of zunyi, guizhou ...   
2680486                                               <NA>   
2680487                                               <NA>   

                                            other_names primary_email  \
0                            [v.i. yurtaev; v. yurtaev]          <NA>   
1                                                   NaN          <NA>   
2                                                   NaN          <NA>   
3                                                   NaN          <NA>   
4                                                   NaN          <NA>   
...                                                 ...           ...   
2680483                                       [wanjala]          <NA>   
2680484                              [xu lu-ang, lu lu]          <NA>   
2680485                                             NaN          <NA>   
2680486                                             NaN          <NA>   
2680487  [zuo xiangang, xiangang zuo, zuo x g, x g zuo]          <NA>   

                                                  keywords  \
0                                                      NaN   
1                                                      NaN   
2                                                      NaN   
3                                                      NaN   
4        [iron chlorosis, fertilizers, calcareous soil,...   
...                                                    ...   
2680483                   [environment and sustainability]   
2680484                                                NaN   
2680485                                                NaN   
2680486                                                NaN   
2680487                                                NaN   

                          external_ids  \
0                                  NaN   
1                                  NaN   
2                                  NaN   
3                                  NaN   
4        [[researcherid, k-4630-2014]]   
...                                ...   
2680483                     

In [115]:
df[df.n_employment != df.n_valid_employment]

orcid  verified_email  verified_primary_email  \
1        0000-0001-6220-5683            True                    True   
2        0000-0001-7071-8294            True                    True   
3        0000-0001-7402-0096            True                    True   
5        0000-0001-8377-3508            True                    True   
8        0000-0002-6508-6998            True                    True   
...                      ...             ...                     ...   
2680476  0000-0001-9133-2366            True                    True   
2680477  0000-0001-8494-2123            True                    True   
2680479  0000-0002-2906-0299            True                    True   
2680481  0000-0002-4422-4036            True                    True   
2680486  0000-0002-3800-6331            True                    True   

        given_names family_name biography                 other_names  \
1              <NA>        <NA>      <NA>                         NaN   
2              <NA>        <NA>      <NA>                         NaN   
3              <NA>        <NA>      <NA>                         NaN   
5              <NA>        <NA>      <NA>  [fontana, milena da silva]   
8              <NA>        <NA>      <NA>                         NaN   
...             ...         ...       ...                         ...   
2680476       søren   staugaard      <NA>                         NaN   
2680477       tarun        jain      <NA>                         NaN   
2680479     tiffany      mackay      <NA>        [tiffany russel sia]   
2680481       vijay    krishnan      <NA>                         NaN   
2680486     zachary    calamari      <NA>                         NaN   

        primary_email                                           keywords  \
1                <NA>                                                NaN   
2                <NA>                                                NaN   
3                <NA>                                                NaN   
5                <NA>               [educação; informática; matemática.]   
8                <NA>                                                NaN   
...               ...                                                ...   
2680476          <NA>                                                NaN   
2680477          <NA>  [pet/ct specialist; nuclear medicine physician...   
2680479          <NA>  [microfluidics, gpc-1, gallium-67, pet/ct, oxy...   
2680481          <NA>                                                NaN   
2680486          <NA>                                                NaN   

                          external_ids  \
1                                  NaN   
2                                  NaN   
3                                  NaN   
5                                  NaN   
8                                  NaN   
...                                ...   
2680476                            NaN   
2680477                            NaN   
2680479  [[researcherid, a-2121-2017]]   
2680481                            NaN   
2680486                            NaN   

                                                 education  \
1                                                      NaN   
2                                                      NaN   
3                                                      NaN   
5                                                      NaN   
8                                                      NaN   
...                                                    ...   
2680476  [[, , aarhus universitet, aarhus, , dk, 1006, ...   
2680477                                                NaN   
2680479  [[faculty of medicine, master in pharmaceutica...   
2680481  [[psychiatry, md, all india institute of medic...   
2680486  [[richard gilder graduate school, phd in compa...   

                                                employment  n_works  \
1        [[research scientist, new york univers

## Biography

In [63]:
df['biography'] = df[df.biography.notna()]['biography'].replace('', np.NaN)

In [64]:
df.biography.describe()

count                                                354015
unique                                               337007
top       car title loans are a more straightforward way...
freq                                                    343
Name: biography, dtype: object

In [65]:
df[(df.biography.notna()) & (df.biography.str.contains('car title loans are a more straightforward'))]

orcid  verified_email  verified_primary_email  \
51306     0000-0002-7397-7977            True                    True   
51307     0000-0003-4931-9736            True                    True   
106024    0000-0001-8221-2303            True                    True   
108770    0000-0001-6736-072X            True                    True   
108771    0000-0002-8727-1246            True                    True   
...                       ...             ...                     ...   
10875416  0000-0002-9640-8136            True                    True   
10878239  0000-0002-6926-3752            True                    True   
10933380  0000-0002-3655-4713            True                    True   
10933381  0000-0002-8724-1020            True                    True   
10985986  0000-0002-4601-4569            True                    True   

           given_names   family_name  \
51306      premium car   title loans   
51307      premium car   title loans   
106024     premium car   title loans   
108770    premium car    title loans   
108771     premium car   title loans   
...                ...           ...   
10875416   premium car   title loans   
10878239   premium car   title loans   
10933380   premium car   title loans   
10933381   premium car   title loans   
10985986   premium car   title loans   

                                                  biography  \
51306     car title loans are a more straightforward way...   
51307     car title loans are a more straightforward way...   
106024    car title loans are a more straightforward way...   
108770    car title loans are a more straightforward way...   
108771    car title loans are a more straightforward way...   
...                                                     ...   
10875416  car title loans are a more straightforward way...   
10878239  car title loans are a more straightforward way...   
10933380  car title loans are a more straightforward way...   
10933381  car title loans are a more straightforward way...   
10985986  car title loans are a more straightforward way...   

                        other_names primary_email  \
51306     [premium car title loans]          <NA>   
51307     [premium car title loans]          <NA>   
106024    [premium car title loans]          <NA>   
108770                          NaN          <NA>   
108771                [loan agency]          <NA>   
...                             ...           ...   
10875416  [premium car title loans]          <NA>   
10878239  [premium car title loans]          <NA>   
10933380  [premium car title loans]          <NA>   
10933381  [premium car title loans]          <NA>   
10985986  [premium car title loans]          <NA>   

                                                   keywords external_ids  \
51306                               [car title loan upland]          NaN   
51307                             [car title loan saratoga]          NaN   
106024                         [car title loan victorville]          NaN   
108770                                                  NaN          NaN   
108771    [refinance car title loan, title loan on car, ...          NaN   
...                                                     ...          ...   
10875416                            [car title loan clovis]          NaN   
10878239                         [car title loan escondido]          NaN   
10933380                        [car title loan san rafael]          NaN   
10933381               [car title loan san juan capistrano]          NaN   
10985986                    [car title loan mount pleasant]          NaN   

         education employment  n_works works_source           activation_date  \
51306          NaN        NaN        0          NaN  2020-11-06t06:10:20.070z   
51307          NaN        NaN        0          NaN  2020-11-13t01:04:19.859z   
106024         NaN        NaN        0          NaN  2020-11-05t00:38:21.096z   
108770         NaN        NaN      

In [66]:
def score(bio):
    try:
        return antispam.score(bio)
    except: # if len(bio) < 3 the filter doesn't know how to handle that
        return -1

In [67]:
df['spam_score'] = df[df.biography.notna()]['biography'].apply(lambda bio: score(bio))

In [68]:
df[df.spam_score == -1][['orcid','biography']]

orcid    biography
25505     0000-0003-0505-2734            j
138487    0000-0002-3417-7299        .....
139595    0000-0003-3794-1288  m.d., ph.d.
193340    0000-0001-9655-4806           肿瘤
194990    0000-0002-9149-0142         be y
...                       ...          ...
10927866  0000-0002-7341-5480        ph.d.
10976080  0000-0003-4041-0840            /
10976689  0000-0002-4285-8537             
10976922  0000-0002-1545-8773           hi
10987379  0000-0002-6302-4224            .

[348 rows x 2 columns]

In [69]:
df['spam_score'] = df['spam_score'].replace(-1, np.NaN)

In [70]:
df.spam_score.describe()

count    3.536670e+05
mean     6.098044e-01
std      4.476618e-01
min      1.917500e-22
25%      1.858235e-02
50%      9.529688e-01
75%      9.999992e-01
max      1.000000e+00
Name: spam_score, dtype: float64

In [71]:
df[df.spam_score > 0.9999][['biography', 'spam_score']]

biography  spam_score
29        investigador de la universidad de oviedo. depa...    1.000000
83        formación académica en la temática de manejo d...    1.000000
217       doctor en educación, maestro en gerencia de la...    1.000000
222       possui graduação em psicologia pela pontifícia...    1.000000
470       roofing contractors in seattle waroofing contr...    1.000000
...                                                     ...         ...
10989593  jose ignacio peláez sánchez ha sido profesor e...    0.999966
10989603  mestranda em tecnologia na saúde e foi aluna o...    1.000000
10989605  the phd degree of pharmacy was received under ...    1.000000
10989615  mostafa metwaly is an assistant lecturer at th...    1.000000
10989617  jual obat aborsi di tangerang, obat penggugur ...    0.999999

[120733 rows x 2 columns]

TODO: offending words, sexually explicit content

## All VS All correlation

In [136]:
fig = px.imshow(df.select_dtypes(include=['bool','number']).fillna(-1).corr())
fig.show()

In [74]:
# df[['verified_email', 
#     'verified_primary_email', 
#     'n_works', 
#     'n_doi',
#     'n_arxiv', 
#     'n_pmc', 
#     'n_other_pids', 
#     'n_emails', 
#     'n_urls', 
#     'n_ids', 
#     'n_keywords', 
#     'n_employment', 
#     'n_education', 
#     'label']].to_pickle('../data/processed/features.pkl')

## Label speculation

In [75]:
df[df.label == 1]

orcid  verified_email  verified_primary_email  \
17        0000-0002-0137-3066            True                    True   
19        0000-0002-0461-9711            True                    True   
22        0000-0002-0761-9450            True                    True   
33        0000-0002-4447-9215            True                    True   
44        0000-0003-0426-4065            True                    True   
...                       ...             ...                     ...   
10989635  0000-0002-7340-9697            True                    True   
10989636  0000-0002-2906-0299            True                    True   
10989637  0000-0001-5896-2024            True                    True   
10989643  0000-0003-2606-0936            True                    True   
10989645  0000-0002-3800-6331            True                    True   

          given_names family_name biography           other_names  \
17               <NA>        <NA>      <NA>                   NaN   
19               <NA>        <NA>      <NA>                   NaN   
22               <NA>        <NA>      <NA>                   NaN   
33               <NA>        <NA>      <NA>                   NaN   
44               <NA>        <NA>      <NA>    [eliza i. gilbert]   
...               ...         ...       ...                   ...   
10989635      tawanda   marandure      <NA>                   NaN   
10989636      tiffany      mackay      <NA>  [tiffany russel sia]   
10989637  giovanni, l      tiscia      <NA>                   NaN   
10989643        luang          xu      <NA>    [xu lu-ang, lu lu]   
10989645      zachary    calamari      <NA>                   NaN   

         primary_email                                           keywords  \
17                <NA>                                                NaN   
19                <NA>                                                NaN   
22                <NA>                                                NaN   
33                <NA>                                                NaN   
44                <NA>                                                NaN   
...                ...                                                ...   
10989635          <NA>                                                NaN   
10989636          <NA>  [microfluidics, gpc-1, gallium-67, pet/ct, oxy...   
10989637          <NA>                                                NaN   
10989643          <NA>                                                NaN   
10989645          <NA>                                                NaN   

                               external_ids  \
17                                      NaN   
19                                      NaN   
22                                      NaN   
33                                      NaN   
44                                      NaN   
...                                     ...   
10989635  [[scopus author id, 48261373600]]   
10989636      [[researcherid, a-2121-2017]]   
10989637  [[scopus author id, 54948242800]]   
10989643                                NaN   
10989645                                NaN   

                                                  education  \
17                                                      NaN   
19                                                      NaN   
22                                                      NaN   
33                                                      NaN   
44                                                      NaN   
...                                                     ...   
10989635  [[animal science, msc sustainable agriculture,...   
10989636  [[faculty of medicine, master in pharmaceutica...   
10989637                                                NaN   
10989643                                                NaN   
10989645  [[richard gilder graduate school, phd in compa...   

                                                 employment  n_works  \

In [76]:
# (df.n_works > 0) & (df.n_ids > 1)

In [77]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10989649 entries, 0 to 10989648
Data columns (total 34 columns):
 #   Column                  Dtype  
---  ------                  -----  
 0   orcid                   object 
 1   verified_email          bool   
 2   verified_primary_email  bool   
 3   given_names             string 
 4   family_name             string 
 5   biography               string 
 6   other_names             object 
 7   primary_email           string 
 8   keywords                object 
 9   external_ids            object 
 10  education               object 
 11  employment              object 
 12  n_works                 Int16  
 13  works_source            object 
 14  activation_date         string 
 15  last_update_date        string 
 16  n_doi                   Int16  
 17  n_arxiv                 Int16  
 18  n_pmc                   Int16  
 19  n_other_pids            Int16  
 20  label                   bool   
 21  primary_email_domain    objec